In [ ]:
import time
import pickle
import pandas as pd 
import numpy as np
from gensim.models import Word2Vec
import gensim
from matplotlib import pyplot as plt
import plotly.graph_objects as go
from nltk.tokenize import word_tokenize
from sklearn.model_selection import train_test_split
from sklearn import preprocessing,naive_bayes, pipeline, manifold 
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.text import text_to_word_sequence
from tensorflow.keras.preprocessing.sequence import pad_sequences
import seaborn as sns
import re
import nltk
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer

In [ ]:
import os
import shutil
for Rand_STATE in [3,7,11,13,15,19,20,27,29,30,35,37,41]:          #First 10 folds of thhese 13 folds are considered
    print("#############################################################")
    print("START ITERATION OF Split Random State: ",Rand_STATE)
    print("#############################################################")
    keys=["API_Data_Adware","API_Data_Agent","API_Data_Backdoor","API_Data_Downloader","API_Data_Ransomware","API_Data_Trojan","API_Data_Virus","API_Data_Worms"]
    TFIDF_Prune_classWise_VAR_Dict={"API_Data_Adware":0.0,"API_Data_Agent":0.0,"API_Data_Backdoor":0.0,"API_Data_Downloader":0.0,"API_Data_Ransomware":0.0,"API_Data_Trojan":0.0,"API_Data_Virus":0.0,"API_Data_Worms":0.0}
    ITE=1
    THRESHOLD=0.95           #F1 Threshold
    #START FLAG TO REMEMBER THE BEST RESULT AND WEIGHTS 
    MAX_F1=0
    BUFF_classWise_VAR_Dict=[]
    REM_ITE=0
    STOP_CNT=5              # wait count
    #END FLAG TO REMEMBER THE BEST RESULT AND WEIGHTS 
    #Model_Result_filenames=["LR_training_output.txt","RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    Model_Result_filenames=["RF_training_output.txt"]
    while True:
        print("#############################################################")
        print("Started Iteration",ITE)

        #CODE for results of previous models END
        %run "VirusShare_willy_ML_BASE_RF.ipynb"
        print("ClassifierName,PRE,REC,F1,ACC")
        #CODE for results of previous models START
        for Mfname in Model_Result_filenames:
            Mfile = open(Mfname) 
            # read the content of the file opened 
            content = Mfile.readlines() 
            #print(content)
            acc=content[22].split()
            scores=content[23].split()
            modelname=Mfname.split('_')[0]
            print(modelname,",",scores[2],",",scores[3],",",scores[4],",",acc[1])
        #EXTRACT F1 SCORES of BASE MODEL for ALL CLASSES 
        Mfile = open("RF_training_output.txt") 
        # read the content of the file opened 
        content = Mfile.readlines() 
        #print(content)
        class_f1=[]
        for I in range(0,8):
            class_f1.append(content[I+13].split()[3])
        class_f1.append(content[23].split()[4])
        print(class_f1)

        #START REMEBER THE BEST F1 SCORE and WEIGHTS
        if(float(class_f1[8])>=MAX_F1):
            MAX_F1=float(class_f1[8])
            REM_ITE=ITE
            BUFF_classWise_VAR_Dict=list(TFIDF_Prune_classWise_VAR_Dict.items())
            STOP_CNT=5
        else:
            STOP_CNT=STOP_CNT-1
        if(STOP_CNT==-1):
            print("MAXIMUM MACRO F1:",MAX_F1,"ITERATION IS: ",REM_ITE)
            print("Weight matrix is: ",BUFF_classWise_VAR_Dict)
            #START Code to move outputs to respective folder of iteration
            DIR_NAME="RS"+str(Rand_STATE)+"_ITE_"+str(ITE)+"OUTPUTS"
            os.makedirs(DIR_NAME)
            eps_files = [f for f in os.listdir() if '.eps' in f.lower()]
            #print(eps_files)
            for eps in eps_files:
                shutil.move(eps, DIR_NAME)
                #shutil.copy(eps, DIR_NAME)
            txt_files = [f for f in os.listdir() if '.txt' in f.lower()]
            #print(eps_files)
            for txt in txt_files:
                shutil.move(txt, DIR_NAME)
                #shutil.copy(txt, DIR_NAME)
            #shutil.copy('Olivera_Bigram_Overlapping_multi_class.ipynb',DIR_NAME)
            print("FINAL TFIDF Prune parameters")
            print(TFIDF_Prune_classWise_VAR_Dict)
            #END Code to move outputs to respective folder of iteration
            break
        #END REMEBER THE BEST F1 SCORE and WEIGHTS

        #print("ECLF,",class0[3],",",class1[3],",",class2[3],",",class3[3],",",class4[3],",",class5[3],",",F1_score[4])
        if(float(class_f1[8])<=THRESHOLD):
            print("TO UPGRADE")
            for I in range(0,8):
                if(class_f1[I]<=class_f1[8]):
                    print("UPGRADE CLASS",I)
                    TFIDF_Prune_classWise_VAR_Dict[keys[I]]=TFIDF_Prune_classWise_VAR_Dict[keys[I]]+0.01
        else:
            print("GOT THE THRESHOLD")
            #START Code to move outputs to respective folder of iteration
            DIR_NAME="RS"+str(Rand_STATE)+"_ITE_"+str(ITE)+"OUTPUTS"
            os.makedirs(DIR_NAME)
            eps_files = [f for f in os.listdir() if '.eps' in f.lower()]
            #print(eps_files)
            for eps in eps_files:
                shutil.move(eps, DIR_NAME)
                #shutil.copy(eps, DIR_NAME)
            txt_files = [f for f in os.listdir() if '.txt' in f.lower()]
            #print(eps_files)
            for txt in txt_files:
                shutil.move(txt, DIR_NAME)
                #shutil.copy(txt, DIR_NAME)
            #shutil.copy('Olivera_Bigram_Overlapping_multi_class.ipynb',DIR_NAME)
            print("FINAL TFIDF Prune parameters")
            print(TFIDF_Prune_classWise_VAR_Dict)
            #END Code to move outputs to respective folder of iteration
            break
        #Code to move outputs to respective folder of iteration
        DIR_NAME="RS"+str(Rand_STATE)+"_ITE_"+str(ITE)+"OUTPUTS"
        os.makedirs(DIR_NAME)
        eps_files = [f for f in os.listdir() if '.eps' in f.lower()]
        #print(eps_files)
        for eps in eps_files:
            shutil.move(eps, DIR_NAME)
            #shutil.copy(eps, DIR_NAME)
        txt_files = [f for f in os.listdir() if '.txt' in f.lower()]
        #print(eps_files)
        for txt in txt_files:
            shutil.move(txt, DIR_NAME)
            #shutil.copy(txt, DIR_NAME)
        #shutil.copy('Olivera_Bigram_Overlapping_multi_class.ipynb',DIR_NAME)
        print("FINAL TFIDF Prune parameters")
        print(TFIDF_Prune_classWise_VAR_Dict)
        print("#############################################################")
        print("Completed Iteration",ITE)
        ITE=ITE+1
    print("#############################################################")
    print("END ITERATION OF Split Random State: ",Rand_STATE)
    print("#############################################################")
print("All Iterations Done")

In [ ]:
print(TFIDF_Prune_classWise_VAR_Dict)


In [ ]:
from matplotlib import pyplot as plt
import numpy as np
#FOR RF   BEST MACRO F1 SCORE in 10-fold validation
#Ite=[3,7,11,13,15,19,20,27,29,30,35,37,41]
#MACRO_F1=[0.93,0.94,0.92,0.89,0.90,0.89,0.92,0.92,0.88,0.91,0.92,0.93,0.92]
Ite=[3,7,11,13,15,19,20,27,29,30]
MACRO_F1=[0.92,0.91,0.92,0.92,0.92,0.91,0.91,0.92,0.91,0.92]

MIN_MACRO_F1=np.min(MACRO_F1)
MAX_MACRO_F1=np.max(MACRO_F1)
MEAN_MACRO_F1=round(np.mean(MACRO_F1),2)

print("10-Fold Validation of MACRO F1 Scores")
print("MINIMUM is: ",MIN_MACRO_F1," Maximum is: ",MAX_MACRO_F1," Mean Macro F1 is: ",MEAN_MACRO_F1," ",round(MEAN_MACRO_F1-MIN_MACRO_F1,2)," ",round(MAX_MACRO_F1-MEAN_MACRO_F1,2))
print("Standard Deviation is: ", round(np.std(MACRO_F1),2))
plt.figure(figsize = (7, 4))

# Plotting a basic histogram
plt.hist(MACRO_F1, bins=10, color='skyblue', edgecolor='black')
 
# Adding labels and title
plt.xlabel('MACRO F1 Scores')
plt.ylabel('Frequency')
#plt.title('Basic Histogram')
plt.savefig("VirusShare_RF_10Fold.eps",format='eps',dpi=1200)
# Display the plot
#plt.show()

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  9  FOLD 1
#Weight matrix is:  [('API_Data_Adware', 0.060000000000000005), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.02), ('API_Data_Downloader', 0.07), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.08)]

#MAXIMUM MACRO F1: 0.91 ITERATION IS:  8  FOLD 2
#Weight matrix is:  [('API_Data_Adware', 0.05), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.0), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.07)]

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  12  FOLD 3
#Weight matrix is:  [('API_Data_Adware', 0.09), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.03), ('API_Data_Downloader', 0.07), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.10999999999999999)]

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  9  FOLD 4
#Weight matrix is:  [('API_Data_Adware', 0.07), ('API_Data_Agent', 0.060000000000000005), ('API_Data_Backdoor', 0.02), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.08)]

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  7  FOLD 5
#Weight matrix is:  [('API_Data_Adware', 0.05), ('API_Data_Agent', 0.060000000000000005), ('API_Data_Backdoor', 0.0), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.060000000000000005)]

#MAXIMUM MACRO F1: 0.91 ITERATION IS:  8  FOLD 6
#Weight matrix is:  [('API_Data_Adware', 0.060000000000000005), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.01), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.07)]

#MAXIMUM MACRO F1: 0.91 ITERATION IS:  8  FOLD 7
#Weight matrix is:  [('API_Data_Adware', 0.05), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.01), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.07)]

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  7  FOLD 8
#Weight matrix is:  [('API_Data_Adware', 0.05), ('API_Data_Agent', 0.060000000000000005), ('API_Data_Backdoor', 0.0), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.060000000000000005)]

#MAXIMUM MACRO F1: 0.91 ITERATION IS:  9  FOLD 9
#Weight matrix is:  [('API_Data_Adware', 0.07), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.02), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.08)]

#MAXIMUM MACRO F1: 0.92 ITERATION IS:  10  FOLD 10
#Weight matrix is:  [('API_Data_Adware', 0.07), ('API_Data_Agent', 0.060000000000000005), ('API_Data_Backdoor', 0.02), ('API_Data_Downloader', 0.060000000000000005), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.08)]

In [ ]:
#CODE FOR EXTRACTING SCORES WITH AFS i.e. The best Iteration of all 10 folds
import os
import shutil
Rand_STATE=[3,7,11,13,15,19,20,27,29,30]    #10 FOLDS
BESt_ITE=[9,8,12,9,7,8,8,7,9,10]            #AFS BEST ITERATION
print("ClassifierName,PRE,REC,F1,ACC")
for LOP_ITE in range(0,10):
    #print("#############################################################")
    #print("Random State: ",Rand_STATE[LOP_ITE]," Best Iteration",BESt_ITE[LOP_ITE])
    #print("#############################################################")
    DIR_NAME="RF_RS"+str(Rand_STATE[LOP_ITE])+"/RS"+str(Rand_STATE[LOP_ITE])+"_ITE_"+str(BESt_ITE[LOP_ITE])+"OUTPUTS"
    #END FLAG TO REMEMBER THE BEST RESULT AND WEIGHTS 
    #Model_Result_filenames=["LR_training_output.txt","RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    #Model_Result_filenames=["RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    Model_Result_filenames=["RF_training_output.txt"]
    
    #CODE for results of previous models START
    for Mfname in Model_Result_filenames:
        fullpath=DIR_NAME+"/"+str(Mfname)
        Mfile = open(fullpath) 
        # read the content of the file opened 
        content = Mfile.readlines() 
        #print(content)
        acc=content[22].split()
        scores=content[23].split()
        modelname=Mfname.split('_')[0]
        print(modelname,",",scores[2],",",scores[3],",",scores[4],",",acc[1])
    #print("#############################################################")
print("All Iterations Done")

In [ ]:
#CODE FOR EXTRACTING SCORES WITHOUT AFS i.e. The best Iteration of all 10 folds
import os
import shutil
Rand_STATE=[3,7,11,13,15,19,20,27,29,30]  #10 FOLDS
#BESt_ITE=[8,8,8,8,8,8,8,8,8,8]   #ITERRAION 1 all weights of CFTW 0 so NO AFS
print("ClassifierName,PRE,REC,F1,ACC")
for LOP_ITE in range(0,10):
    #print("#############################################################")
    #print("Random State: ",Rand_STATE[LOP_ITE]," Best Iteration",BESt_ITE[LOP_ITE])
    #print("#############################################################")
    DIR_NAME="RF_RS"+str(Rand_STATE[LOP_ITE])+"/RS"+str(Rand_STATE[LOP_ITE])+"_ITE_1OUTPUTS"   #1st Iteration Always
    #END FLAG TO REMEMBER THE BEST RESULT AND WEIGHTS 
    #Model_Result_filenames=["LR_training_output.txt","RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    #Model_Result_filenames=["RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    Model_Result_filenames=["RF_training_output.txt"]
    
    #CODE for results of previous models START
    for Mfname in Model_Result_filenames:
        fullpath=DIR_NAME+"/"+str(Mfname)
        Mfile = open(fullpath) 
        # read the content of the file opened 
        content = Mfile.readlines() 
        #print(content)
        acc=content[22].split()
        scores=content[23].split()
        modelname=Mfname.split('_')[0]
        print(modelname,",",scores[2],",",scores[3],",",scores[4],",",acc[1])
    #print("#############################################################")
print("All Iterations Done")

In [ ]:
#MAXIMUM MACRO F1: 0.92 ITERATION IS:  9  RS  3
#Weight matrix is:  [('API_Data_Adware', 0.060000000000000005), ('API_Data_Agent', 0.07), ('API_Data_Backdoor', 0.02), ('API_Data_Downloader', 0.07), ('API_Data_Ransomware', 0.0), ('API_Data_Trojan', 0.0), ('API_Data_Virus', 0.0), ('API_Data_Worms', 0.08)]
#FOR RF
import os
import shutil
from matplotlib import pyplot as plt
import numpy as np
Ite=[1,2,3,4,5,6,7,8,9,10,11,12,13,14,15]
Rand_STATE=[3]
BESt_ITE=[9]
RESARR=[]
print("ClassifierName,PRE,REC,F1,ACC")
for LOP_ITE in range(1,16):
    #print("#############################################################")
    #print("Random State: ",Rand_STATE[LOP_ITE]," Best Iteration",BESt_ITE[LOP_ITE])
    #print("#############################################################")
    DIR_NAME="RF_RS"+str(Rand_STATE[0])+"/RS"+str(Rand_STATE[0])+"_ITE_"+str(LOP_ITE)+"OUTPUTS"
    #END FLAG TO REMEMBER THE BEST RESULT AND WEIGHTS 
    #Model_Result_filenames=["LR_training_output.txt","RF_training_output.txt","SVC_training_output.txt","KNN_training_output.txt","ECLF_training_output.txt"]
    #EXTRACT F1 SCORES of BASE MODEL for ALL CLASSES 
    Mfile = open(DIR_NAME+"/"+"RF_training_output.txt") 
    content = Mfile.readlines() 
    #print(content)
    class_f1=[]
    for I in range(0,8):
        class_f1.append(content[I+13].split()[3])
    class_f1.append(content[23].split()[4])
    RESARR.append(class_f1)
    #print(class_f1)
print("All Iterations Done")
#print(RESARR)

CLASS0=[]
CLASS1=[]
CLASS2=[]
CLASS3=[]
CLASS4=[]
CLASS5=[]
CLASS6=[]
CLASS7=[]
MACRO=[]
for X in RESARR:
    CLASS0.append(float(X[0]))
    CLASS1.append(float(X[1]))
    CLASS2.append(float(X[2]))
    CLASS3.append(float(X[3]))
    CLASS4.append(float(X[4]))
    CLASS5.append(float(X[5]))
    CLASS6.append(float(X[6]))
    CLASS7.append(float(X[7]))
    MACRO.append(float(X[8]))

plt.figure(figsize = (7, 4))
#plt.title(dfname_str)
# Define axes labels
plt.xlabel("Iteration")
plt.ylabel("F1 Score of RF")
plt.xticks(range(1,16))
plt.plot(Ite, CLASS0, "aqua", label="Adware")   
plt.plot(Ite, CLASS1, "darkorange",label="Agent")  
plt.plot(Ite, CLASS2,"cornflowerblue",label="Backdoor")  
plt.plot(Ite, CLASS3,"blue",label="Downloader")
plt.plot(Ite, CLASS4,"red",label="Ransomware")  
plt.plot(Ite, CLASS5,"green",label="Trojan")  
plt.plot(Ite, CLASS6,"lightgreen",label="Virus")  
plt.plot(Ite, CLASS7,"gray",label="Worms")  
plt.plot(Ite, MACRO,"magenta",label="MACRO")  

#Vertical Line for the best MACRO F1
plt.axvline(x = 9, color = 'black',ymin = 0, ymax = 0.95, label = 'Iteration with Optimum MACRO F1')

plt.legend(loc="lower right",ncol=2,fancybox=True)
# Displaying the line chart  
#plt.show()   
plt.savefig("RF_VirusShare_Change_in_RF_F1Scores.eps",format='eps',dpi=1200)   